## CREATING GOLDEN TESTSET ##

In [1]:
%pip install -qU langsmith langchain-core==0.2.40 langchain-community langchain-openai langchain-qdrant

Note: you may need to restart the kernel to use updated packages.


In [2]:
%pip install -qU pymupdf ragas

Note: you may need to restart the kernel to use updated packages.


In [3]:
import os
from dotenv import load_dotenv
from langchain_community.document_loaders import PyMuPDFLoader
from ragas.testset.generator import TestsetGenerator
from ragas.testset.evolutions import simple, reasoning, multi_context
from langchain_openai import ChatOpenAI, OpenAIEmbeddings
from langsmith import Client
import getpass
from uuid import uuid4

# Load environment variables
load_dotenv()

# Set up API keys
os.environ["LANGCHAIN_TRACING_V2"] = "true"
os.environ["LANGCHAIN_API_KEY"] = getpass.getpass("LangChain API Key:")
os.environ["LANGCHAIN_PROJECT"] = f"AI_Ethics_Framework_Analysis_{uuid4().hex[:8]}"
os.environ["OPENAI_API_KEY"] = getpass.getpass("OpenAI API Key:")



/opt/homebrew/Caskroom/miniforge/base/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
# Load documents
documents = PyMuPDFLoader(file_path="https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf").load()


In [5]:
from langchain_community.document_loaders import PyMuPDFLoader

pdf_links = [
    "https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf",
    "https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf"
]

documents = []
for link in pdf_links:
    loader = PyMuPDFLoader(file_path=link)
    documents.extend(loader.load())
# Set up LLMs and embeddings
generator_llm = ChatOpenAI(model="gpt-3.5-turbo")
critic_llm = ChatOpenAI(model="gpt-4o-mini")
embeddings = OpenAIEmbeddings()

# Create TestsetGenerator
generator = TestsetGenerator.from_langchain(
    generator_llm,
    critic_llm,
    embeddings
)

# Define distributions
distributions = {
    simple: 0.5,
    multi_context: 0.4,
    reasoning: 0.1
}

# Generate testset
testset = generator.generate_with_langchain_docs(documents, 20, distributions, with_debugging_logs=True)


embedding nodes:   5%|▍         | 14/284 [00:00<00:14, 19.08it/s][ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Automated systems', 'Disparity assessment', 'Disparity mitigation', 'Algorithmic discrimination', 'Ongoing monitoring']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Racial equity', 'Supreme Court Decision', 'Automated society', 'Privacy protection', 'Crime prediction software']}
embedding nodes:   6%|▌         | 17/284 [00:00<00:12, 21.58it/s][ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['GAI incidents', 'AI Actors', 'Incident reporting', 'Documentation practices', 'Information sharing']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Automated systems', 'Algorithmic discrimination', 'Equity assessment', 'Representative data', 'Guarding against proxies']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Policies and procedures', 'Human-AI configurations', 'Oversight of AI systems', 'GAI risks', 'Threat modeling']}
embedding n

In [6]:
from datetime import datetime

if testset is not None:
    # Create LangSmith dataset with a timestamp
    try:
        client = Client()
        timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
        dataset_name = f"AI Ethics Framework Testset_{timestamp}"
        dataset = client.create_dataset(
            dataset_name=dataset_name,
            description="Questions about AI Ethics Frameworks"
        )

        # Add examples to dataset
        for test in testset.to_pandas().iterrows():
            client.create_example(
                inputs={
                    "question": test[1]["question"]
                },
                outputs={
                    "answer": test[1]["ground_truth"]
                },
                metadata={
                    "context": test[0]
                },
                dataset_id=dataset.id
            )

        print(f"Synthetic dataset generated and uploaded to LangSmith as '{dataset_name}'.")
    except Exception as e:
        print(f"Error uploading to LangSmith: {str(e)}")
else:
    print("Failed to generate testset. Cannot upload to LangSmith.")

Synthetic dataset generated and uploaded to LangSmith as 'AI Ethics Framework Testset_20240919_103614'.


## LOOK AT WEEK 4 DAY 2 FOR GUIDANCE ON EDITING BELOW CODE ##


In [7]:
%pip install -qU qdrant-client pymupdf pandas

Note: you may need to restart the kernel to use updated packages.


In [8]:
import os
import openai
from getpass import getpass

openai.api_key = getpass("Please provide your OpenAI Key: ")
os.environ["OPENAI_API_KEY"] = openai.api_key

In [ ]:
PDF_LINK = "https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf"

loader = PyMuPDFLoader(PDF_LINK)

documents = loader.load()

In [9]:
pdf_links = [
    "https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf",
    "https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf"
]

documents = []
for link in pdf_links:
    loader = PyMuPDFLoader(file_path=link)
    documents.extend(loader.load())

In [ ]:
documents[0].metadata

{'source': 'https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf',
 'file_path': 'https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf',
 'page': 0,
 'total_pages': 64,
 'format': 'PDF 1.6',
 'title': 'Artificial Intelligence Risk Management Framework: Generative Artificial Intelligence Profile',
 'author': 'National Institute of Standards and Technology',
 'subject': '',
 'keywords': '',
 'creator': 'Acrobat PDFMaker 24 for Word',
 'producer': 'Adobe PDF Library 24.2.159',
 'creationDate': "D:20240805141702-04'00'",
 'modDate': "D:20240805143048-04'00'",
 'trapped': ''}

In [10]:
# Find the index where the second document starts
second_doc_start = next(i for i, doc in enumerate(documents) if doc.metadata['source'] != documents[0].metadata['source'])

print("Metadata for the first document:")
print(documents[0].metadata)

print("\nMetadata for the second document:")
print(documents[second_doc_start].metadata)

Metadata for the first document:
{'source': 'https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf', 'file_path': 'https://nvlpubs.nist.gov/nistpubs/ai/NIST.AI.600-1.pdf', 'page': 0, 'total_pages': 64, 'format': 'PDF 1.6', 'title': 'Artificial Intelligence Risk Management Framework: Generative Artificial Intelligence Profile', 'author': 'National Institute of Standards and Technology', 'subject': '', 'keywords': '', 'creator': 'Acrobat PDFMaker 24 for Word', 'producer': 'Adobe PDF Library 24.2.159', 'creationDate': "D:20240805141702-04'00'", 'modDate': "D:20240805143048-04'00'", 'trapped': ''}

Metadata for the second document:
{'source': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'file_path': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'page': 0, 'total_pages': 73, 'format': 'PDF 1.6', 'title': 'Blueprint for an AI Bill of Rights', 'author': '', 'subject': '', 'keywords': '', 'cre

In [11]:
#Chunking the docs 

from langchain.text_splitter import RecursiveCharacterTextSplitter

CHUNK_SIZE = 500
CHUNK_OVERLAP = 40

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=CHUNK_SIZE,
    chunk_overlap=CHUNK_OVERLAP,
    length_function=len,
    is_separator_regex=False
)

documents = text_splitter.split_documents(documents)

len(documents)

909

In [12]:
#Establishing embedding model to evaluate 
from langchain_openai import OpenAIEmbeddings

EMBEDDING_MODEL = "text-embedding-ada-002"

embeddings = OpenAIEmbeddings(
    model=EMBEDDING_MODEL,
    openai_api_key=openai.api_key
)

In [13]:
#Setting up the vector store

from langchain_qdrant import QdrantVectorStore
from qdrant_client import QdrantClient
from qdrant_client.http.models import Distance, VectorParams

LOCATION = ":memory:"
COLLECTION_NAME = "AI_Ethics_Framework"
VECTOR_SIZE = 1536

In [14]:
#Creating the collection in Qdrant

qdrant_client = QdrantClient(location=LOCATION)

qdrant_client.create_collection(
    collection_name=COLLECTION_NAME,
    vectors_config=VectorParams(size=VECTOR_SIZE, distance=Distance.COSINE),
)

qdrant_vector_store = QdrantVectorStore(
    client=qdrant_client,
    collection_name=COLLECTION_NAME,
    embedding=embeddings
)

qdrant_vector_store.add_documents(documents)

['baf78acdfa114abd87b15abfd26bf62c',
 'e4e58eae86014ce3b9475e8fb6a63a1d',
 '6cd54a4774ee4706aec17907d0ee1a1d',
 'e7efe529eae8414f8535d46fa6510f2a',
 '5489fc780a1e479ba4dd5dbc273bb632',
 '0e535db2d41c4eb8851efdc7a144e1cc',
 'e2fde5029dcd4b498c89761afe9c3ad6',
 '8bbd8857aaa1417b859c6bf36b6ff1dc',
 '54b40c8055c04894bbf7ce0da3010eaa',
 '30376a09e62142a79b03d089e87836be',
 '26ebec3c14614368bcf68a56235790fa',
 'ff20a198f82f4c5785e33e3f801ce24e',
 '3659272848a542b1bf77bd5f70203b6d',
 '9af72f5fa50a4d77ac40ece4caed7c27',
 '8414f52b3c914e8e91e294f191b9ecc7',
 'db2a3d673b8f4ffca095e5b7b7758da8',
 '5ad9659f6cdc41ee972b1ad52a5073d3',
 '4d00aeac88074bd291e433a2b4cadaf3',
 '58a10602d54640559c695b98112de5d6',
 '5b2558290d9744f49a40ef689645f14e',
 '266f94af1bef4052961840fbf4d127a4',
 '9ee8b2c9177b4bbab2f2d96e91cfd9b2',
 '7af0f6f7abea453ea89b4d2c7df067d2',
 'e399052b679c48c882d46f419475dd0d',
 'fde9c44d3877411398793826cf77f006',
 'bb65149d62e047a4b953a45b5c3464b5',
 'da3a13a03d204510bfd721c8a6f0d7c9',
 

In [15]:
#Creating the retriever

retriever = qdrant_vector_store.as_retriever()

In [16]:
#Test retriever

retrieved_documents = retriever.invoke("What is Artificial Intelligence?")

for doc in retrieved_documents:
  print(doc)

page_content='generation of artificially intelligent partners.95 The National Science Foundation’s program on Fairness in 
Artificial Intelligence also includes a specific interest in research foundations for explainable AI.96
45' metadata={'source': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'file_path': 'https://www.whitehouse.gov/wp-content/uploads/2022/10/Blueprint-for-an-AI-Bill-of-Rights.pdf', 'page': 44, 'total_pages': 73, 'format': 'PDF 1.6', 'title': 'Blueprint for an AI Bill of Rights', 'author': '', 'subject': '', 'keywords': '', 'creator': 'Adobe Illustrator 26.3 (Macintosh)', 'producer': 'iLovePDF', 'creationDate': "D:20220920133035-04'00'", 'modDate': "D:20221003104118-04'00'", 'trapped': '', '_id': '6d503f2d124d493dbb4a5bf68887736e', '_collection_name': 'AI_Ethics_Framework'}
page_content='Artiﬁcial Intelligence. https://www.whitehouse.gov/brieﬁng-room/presidential-
actions/2023/10/30/executive-order-on-the-safe-secure

In [17]:
from langchain.prompts import ChatPromptTemplate

template = """
You are an expert AI assistant with deep knowledge of business, technology, and entrepreneurship. Your task is to provide accurate, insightful answers based solely on the given context. Follow these guidelines:

1. Analyze the question carefully to understand the core information being sought.
2. Thoroughly examine the provided context, identifying key relevant information.
3. Formulate a clear, concise answer that directly addresses the question.
4. Use specific details and examples from the context to support your answer.
5. If the context doesn't contain sufficient information to fully answer the question, state this clearly and say,'I don't know'.
6. Do not introduce any information not present in the context.
7. If asked for an opinion or recommendation, base it strictly on insights from the context.
8. Use a confident, authoritative tone while maintaining accuracy.
9. If you cannot provide a clear answer to the question, reply with "I don't know".

Question:
{question}

Context:
{context}

Answer:
"""

prompt = ChatPromptTemplate.from_template(template)

In [19]:
#Instantiating RAG chain
from operator import itemgetter
from langchain_openai import ChatOpenAI
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough

primary_qa_llm = ChatOpenAI(model_name="gpt-4o-mini", temperature=0)

retrieval_augmented_qa_chain = (
    {"context": itemgetter("question") | retriever, "question": itemgetter("question")}
    | RunnablePassthrough.assign(context=itemgetter("context"))
    | {"response": prompt | primary_qa_llm, "context": itemgetter("context")}
)

In [21]:
question = "What is Artificial Intelligence?"

result = retrieval_augmented_qa_chain.invoke({"question" : question})

print(result["response"].content)

I don't know.


In [22]:
testset_df = testset.to_pandas()
testset_df.to_csv("testset.csv")

In [23]:
import pandas as pd

test_df = pd.read_csv("testset.csv")

In [24]:
test_df

Unnamed: 0                                           question  \
0            0  What role does human oversight play in ensurin...   
1            1  What are the risks associated with confabulati...   
2            2  How can digital transparency mechanisms like p...   
3            3  How can organizations measure performance, cap...   
4            4  What is the role of responsible AI ventures in...   
5            5  What are some examples of enforcement actions ...   
6            6  Who are some of the stakeholders that submitte...   
7            7  How can the principles of data privacy be impl...   
8            8  How can Generative AI systems potentially faci...   
9            9  How do advertisement delivery systems reinforc...   
10          10  Why is assessing content lineage and origin im...   
11          11  How can stakeholders prevent algorithmic discr...   
12          12  What restrictions does the Biometric Informati...   
13          13          How do ad systems perpetuate stereotypes?   
14          14  What role does public input play in developing...   
15          15  What strategies do responsible AI ventures use...   
16          16  How can feedback and red-teaming ensure fair G...   
17          17  How can public feedback improve pre-deployment...   
18          18  How can privacy be ensured in automated system...   

                                             contexts  \
0   [' \n \n \n \n \n \n \nHUMAN ALTERNATIVES, \nC...   
1   [' \n6 \n2.2. Confabulation \n“Confabulation” ...   
2   [' \n51 \ngeneral public participants. For exa...   
3   [' \n49 \nearly lifecycle TEVV approaches are ...   
4   [' \nENDNOTES\n12. Expectations about reportin...   
5   [" \n65. See, e.g., Scott Ikeda. Major Data Br...   
6   ['APPENDIX\nSummaries of Additional Engagement...   
7   [' \n \n \n \n \n \n \n \n \n \n \n \n \n \n \...   
8   [' \n10 \nGAI systems can ease the unintention...   
9   [' \n \n  \nWHY THIS PRINCIPLE IS IMPORTANT\nT...   
10  [' \n25 \nMP-2.3-002 Review and document accur...   
11  [' \xad\xad\xad\xad\xad\xad\xad\nALGORITHMIC D...   
12  [' \n \n \n \n \n \n \n \n \n \n \n \n \n \n \...   
13  [' \n \n  \nWHY THIS PRINCIPLE IS IMPORTANT\nT...   
14  [' \n \n \n \n \n  \n \n \n \n \n \n \n \n \n ...   
15  [' \nENDNOTES\n12. Expectations about reportin...   
16  [' \n29 \nMS-1.1-006 \nImplement continuous mo...   
17  [' \n49 \nearly lifecycle TEVV approaches are ...   
18  [' \n \n \n \n \n \nDATA PRIVACY \nWHAT SHOULD...   

                                         ground_truth evolution_type  \
0   Human oversight plays a crucial role in ensuri...         simple   
1   Risks from confabulations in GAI systems inclu...         simple   
2   Digital transparency mechanisms like provenanc...         simple   
3   Organizations can measure performance, capabil...         simple   
4   Responsible AI ventures play a crucial role in...         simple   
5   Some examples of enforcement actions taken by ...         simple   
6   The stakeholders that submitted responses to t...         simple   
7   Real-life examples of how data privacy princip...         simple   
8   Generative AI systems can potentially facilita...         simple   
9   Advertisement delivery systems reinforce racia...         simple   
10  Assessing content lineage and origin in GAI sy...  multi_context   
11  Stakeholders can prevent algorithmic discrimin...  multi_context   
12  No private entity in Illinois may collect, cap...  multi_context   
13  Advertisement delivery systems perpetuate ster...  multi_context   
14  The answer to given question is not present in...  multi_context   
15  Responsible AI ventures use various strategies...  multi_context   
16  Feedback and red-teaming can ensure fair GAI o...  multi_context   
17  Public feedback can improve pre-deployment tes...  multi_context   
18  Privacy in automated system design can be ensu...      reasoning   

                                         

In [25]:
test_questions = test_df["question"].values.tolist()
test_groundtruths = test_df["ground_truth"].values.tolist()

In [26]:
answers = []
contexts = []

for question in test_questions:
  response = retrieval_augmented_qa_chain.invoke({"question" : question})
  answers.append(response["response"].content)
  contexts.append([context.page_content for context in response["context"]])

In [27]:
from datasets import Dataset

response_dataset = Dataset.from_dict({
    "question" : test_questions,
    "answer" : answers,
    "contexts" : contexts,
    "ground_truth" : test_groundtruths
})

In [28]:
response_dataset[0]

{'question': 'What role does human oversight play in ensuring the ethical use of automated systems within sensitive domains?',
 'answer': "Human oversight plays a crucial role in ensuring the ethical use of automated systems within sensitive domains, as highlighted in the context provided. These domains, such as healthcare and public benefits, require additional protections due to the potential for unfair, inaccurate, or dangerous outcomes if automated systems are used without adequate safeguards.\n\nExtensive human oversight is essential to monitor and evaluate the performance of these systems, ensuring that they operate safely and effectively. This oversight includes implementing fallback systems that allow for timely human consideration and remedy when automated decisions are made. Furthermore, there should be mechanisms in place for individuals to opt out of automated systems in favor of human alternatives, where appropriate.\n\nAdditionally, ongoing training and assessment of huma

In [29]:
from ragas import evaluate
from ragas.metrics import (
    faithfulness,
    answer_relevancy,
    answer_correctness,
    context_recall,
    context_precision,
)

metrics = [
    faithfulness,
    answer_relevancy,
    context_recall,
    context_precision,
    answer_correctness,
]

In [30]:
results = evaluate(response_dataset, metrics)

Evaluating: 100%|██████████| 95/95 [01:08<00:00,  1.38it/s]


In [31]:
results

{'faithfulness': 0.8091, 'answer_relevancy': 0.9646, 'context_recall': 0.6860, 'context_precision': 0.8582, 'answer_correctness': 0.7387}

In [32]:
results_df = results.to_pandas()
results_df

question  \
0   What role does human oversight play in ensurin...   
1   What are the risks associated with confabulati...   
2   How can digital transparency mechanisms like p...   
3   How can organizations measure performance, cap...   
4   What is the role of responsible AI ventures in...   
5   What are some examples of enforcement actions ...   
6   Who are some of the stakeholders that submitte...   
7   How can the principles of data privacy be impl...   
8   How can Generative AI systems potentially faci...   
9   How do advertisement delivery systems reinforc...   
10  Why is assessing content lineage and origin im...   
11  How can stakeholders prevent algorithmic discr...   
12  What restrictions does the Biometric Informati...   
13          How do ad systems perpetuate stereotypes?   
14  What role does public input play in developing...   
15  What strategies do responsible AI ventures use...   
16  How can feedback and red-teaming ensure fair G...   
17  How can public feedback improve pre-deployment...   
18  How can privacy be ensured in automated system...   

                                             contexts  \
0   [diagnose disease. Absent appropriate safeguar...   
1   [many real-world applications, such as in heal...   
2   [A.1.6. Content Provenance \nOverview \nGAI te...   
3   [materials (SBOMs), application of service lev...   
4   [and implement measures to prevent similar one...   
5   [unions-1658603\n68. See, e.g., enforcement ac...   
6   [Biometric Technologies. Accessed Apr. 19, 202...   
7   [DATA PRIVACY \nHOW THESE PRINCIPLES CAN MOVE ...   
8   [Disinformation and misinformation – both of w...   
9   [ering ads in ways that reinforce racial and g...   
10  [A.1.6. Content Provenance \nOverview \nGAI te...   
11  [systems have the capacity to drive extraordin...   
12  [tion is used. The Biometric Information Priva...   
13  [ering ads in ways that reinforce racial and g...   
14  [discussions, public listening sessions, priva...   
15  [campaigns, which may not be photorealistic, b...   
16  [subjects research requirements, and best prac...   
17  [as through AI red-teaming.  \nIntegrating pre...   
18  [Privacy by design and by default. Automated s...   

                                               answer  \
0   Human oversight plays a crucial role in ensuri...   
1   The risks associated with confabulations in Ge...   
2   Digital transparency mechanisms, such as prove...   
3   Organizations can measure performance, capabil...   
4   Responsible AI ventures play a crucial role in...   
5   Some examples of enforcement actions taken by ...   
6   Some of the stakeholders that submitted respon...   
7   The principles of data privacy can be implemen...   
8   Generative AI (GAI) systems can facilitate the...   
9   Advertisement delivery systems reinforce racia...   
10  Assessing content lineage and origin in Genera...   
11  Stakeholders can prevent algorithmic discrimin...   
12  The Biometric Information Privacy Act (BIPA) i...   
13  Ad systems perpetuate stereotypes by directing...   
14  Public input plays a crucial role in developin...   
15  Responsible AI ventures implement several stra...   
16  Feedback and red-teaming can ensure fair Gener...   
17  Public feedback can significantly enhance pre-...   
18  Privacy can be ensured in automated system des...   

                                         ground_truth  faithfulness  \
0   Human oversight plays a crucial role in ensuri...      1.000000   
1   Risks from confabulations in GAI systems inclu...      0.900000   
2   Digital transparency mechanisms like provenanc...      0.846154   
3   Organizations can measure performance, capabil...      1.000000   
4   Responsible AI ventures play a crucial role in...      0.055556   
5   Some examples of enforcement actions taken by ...      1.000000   
6   The stakeholders that submitted responses to t...      0.500000   
7   Real-life examples of how data privacy princip... 

In [35]:
# Now, convert the results DataFrame to a Hugging Face Dataset
dataset = Dataset.from_pandas(results_df)

def format_for_hf(example):
    return {
        'input_text': f"Question: {example['question']}\nContext: {example['contexts']}",
        'target_text': example['ground_truth'],
        'faithfulness': example['faithfulness'],
        'answer_relevancy': example['answer_relevancy'],
        'context_recall': example['context_recall'],
        'context_precision': example['context_precision'],
        'answer_correctness': example['answer_correctness']
    }

formatted_dataset = dataset.map(format_for_hf)

# Optional: Filter low-scoring entries
def filter_low_scores(example):
    return example['faithfulness'] > 0.5 and example['answer_correctness'] > 0.5

filtered_dataset = formatted_dataset.filter(filter_low_scores)

# Split the dataset
train_test = filtered_dataset.train_test_split(test_size=0.2)

# Save the datasets
train_test['train'].save_to_disk("/Users/annatucker/Workspace/AIE4Midterm/train_dataset")
train_test['test'].save_to_disk("/Users/annatucker/Workspace/AIE4Midterm/test_dataset")


# Print some statistics
print(f"Train dataset size: {len(train_test['train'])}")
print(f"Test dataset size: {len(train_test['test'])}")
print(f"Sample entry:\n{train_test['train'][0]}")

Saving the dataset (1/1 shards): 100%|██████████| 4/4 [00:00<00:00, 1311.44 examples/s]

Train dataset size: 13
Test dataset size: 4
Sample entry:
{'question': 'How can privacy be ensured in automated system design?', 'contexts': ['Privacy by design and by default. Automated systems should be designed and built with privacy protect\xad\ned by default. Privacy risks should be assessed throughout the development life cycle, including privacy risks \nfrom reidentification, and appropriate technical and policy mitigation measures should be implemented. This \nincludes potential harms to those who are not users of the automated system, but who may be harmed by', 'Demonstrate the safety and effectiveness of the system \nIndependent evaluation. Automated systems should be designed to allow for independent evaluation (e.g., \nvia application programming interfaces). Independent evaluators, such as researchers, journalists, ethics \nreview boards, inspectors general, and third-party auditors, should be given access to the system and samples \nof associated data, in a manner consist